In [89]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl

## Relevant Equations:

Pressure distribution:

$p = p_{0} - \Delta pe^{r^2/R^2}$


Geostrophic Balance:
$f\hat{\mathbf{k}}\times \vec{u} = -\frac{1}{\rho}\nabla p$

In [125]:
## Constants
lat = 39 #degrees
omega = 7.29e-5 #rad/sec
f = 2*omega*np.sin(np.radians(lat))
R = 100e3
dP = 50 #hPa
rho = 1.225
p_0 = 1000
print(f)

9.175491301506629e-05


In [126]:
## Hurricane ODE:

def GaussODE(t,y): 
    global f, R, rho, dP
    rx = y[0]
    ry = y[1]
    vx = y[2]
    vy = y[3]
 
    drxdt = vx
    drydt = vy
    
    a_p = -200/(R**2*rho) * dP * np.e**(-(rx**2+ry**2)/R**2)
    a_corx = f*vy
    a_cory = -f*vx
    dvxdt = a_p * rx + a_corx
    dvydt = a_p * ry + a_cory
     
    dydt = np.array([drxdt,drydt,dvxdt,dvydt])
    return dydt

In [127]:
rs = np.linspace(5000,200000,12)

def find_zero(r):
    grad = -200 /(R**2*rho) * dP * np.e**(-((r)/R)**2)
    v = ((-f+np.sqrt(f**2-4*grad))/2) * r
    return v

velocities = find_zero(rs)
print(velocities)

[ 4.28833616 18.99520948 31.87433518 41.79350557 48.0516533  50.44714218
 49.25335359 45.11720044 38.91202024 31.58222949 24.01285182 16.94444971]


In [132]:
x = np.linspace(0,2e5)
y = p_0 - dP*np.exp(-(x**2/R**2))
plt.plot(x/1000,y)
plt.title('Air Pressure vs. Radius')
plt.xlabel('Radius (km)')
plt.ylabel('Pressure (hPa)')
plt.savefig('Gaussianpressure.jpg')

In [129]:
y = np.zeros([len(rs),4])
for i in range(len(rs)):
    y[i,0] = rs[i]
    y[i,3] = velocities[i]

tMax = 1e5
dt = 2

locations = np.zeros([len(rs),2,int(tMax/dt)])

for i in range(len(rs)):
    t = 0
    t_index = -1
    y_use = y[i,:]
    while (t < tMax):
        t += dt
        t_index += 1
        F1 = GaussODE(t,y_use)
        F2 = GaussODE(t+dt/2.0, y_use + dt/2 * F1)
        F3 = GaussODE(t+dt/2.0, y_use + dt/2 * F2)
        F4 = GaussODE(t+dt, y_use + dt*F3)
        dydt = 1/6 * (F1 + 2*F2 + 2*F3 + F4)*dt
        
        for j in range(len(y_use)):
            y_use[j] = y_use[j] + dydt[j]
        
        locations[i,0,t_index] = y_use[0]
        locations[i,1,t_index] = y_use[1]
    

for i in range(len(rs)):
    plt.plot(locations[i,0,:],locations[i,1,:])
    
plt.show()

In [130]:
%matplotlib osx
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Hurricane')
writer = FFMpegWriter(fps=25, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi = 200)
ax = fig.add_subplot(111)

dims = np.shape(locations)
colors = ['black','yellow','steelblue','dimgray','gainsboro','teal','lightcoral','violet','greenyellow',
          'maroon','red','turquoise']
lag = 400


with writer.saving(fig, "GaussHurricane1.mp4", dpi=400):
    nf = 500
    for i in range(nf):
        fig.clear()
        if i*50 <= lag:
            for j in range(len(rs)):
                plt.plot(locations[j,0,0:i*50]/1000,locations[j,1,0:i*50]/1000, '-', color = colors[j])
                plt.plot(locations[j,0,i*50]/1000,locations[j,1,i*50]/1000, 'o', color = colors[j])
        else:
            for j in range(len(rs)):
                plt.plot(locations[j,0,i*50-lag:i*50]/1000,locations[j,1,i*50-lag:i*50]/1000, 
                         '-', color = colors[j])
                plt.plot(locations[j,0,i*50]/1000,locations[j,1,i*50]/1000, 'o', color = colors[j])
        plt.xlim((-220, 220))
        plt.ylim((-220, 220))
        plt.title('Test Particles in Hurricane after t = {0:04f} hours'.format((i*50)*2/(60*60)), loc = 'left')
        plt.xlabel('Kilometers')
        plt.ylabel('Kilometers')
        plt.show()
        plt.draw()
        plt.pause(.01)
        writer.grab_frame()

In [104]:
## Velocity field:

r = np.linspace(0,400,100)
vs = find_zero(1000*r)

plt.plot(r,vs)
plt.title('Velocity vs. Radius for Gaussian Pressure Gradient')
plt.xlabel('Radius (km)')
plt.ylabel('Wind Velocity (m/s)')
plt.show()
plt.savefig('VelocityvsRad.jpg', dpi = 500)

In [103]:
N = 501
A = np.zeros((N,N))
for i in range(N):
    for j in range(N):
        r = 1000*np.sqrt((250-i)**2+(250-j)**2)
        A[i,j] = find_zero(r)
        
im = plt.imshow(A, cmap="cividis")
plt.xlabel('km')
plt.ylabel('km')
plt.title('Wind Velocity Field')

cbar = plt.colorbar(im)
cbar.set_label("Velocity (m/s)")
plt.savefig('VelocityField.jpg', dpi = 500)

In [ ]:
## Hurricane ODE:

def LinearODE(t,y): 
    global f, R, rho, dP
    rx = y[0]
    ry = y[1]
    vx = y[2]
    vy = y[3]
 
    drxdt = vx
    drydt = vy
    
    a_p = -5e-4/rho/np.sqrt(rx**2+ry**2)
    a_corx = f*vy
    a_cory = -f*vx
    dvxdt = a_p * rx + a_corx
    dvydt = a_p * ry + a_cory
     
    dydt = np.array([drxdt,drydt,dvxdt,dvydt])
    return dydt

In [109]:
def find_zeros_lin(r):
    grad = -5e-4/rho
    v = ((-f+np.sqrt(f**2-4*grad/r))/2) * r
    return v

print(find_zeros_lin(rs*1000))

[4.40609144 4.43895875 4.44308943 4.44470716 4.44557027 4.4461069
 4.44647284 4.44673835 4.44693978 4.44709784 4.44722517 4.44732994]
